## Imports

* duckdb :DuckDB Python API can be installed using pip: pip install duckdb.

* Get duckdb :https://duckdb.org/

In [13]:
import duckdb as dcb

## Geting the data
* from SOURCE COOPERATIVE :https://beta.source.coop/repositories/vida/google-microsoft-open-buildings/description/

In [2]:
dcb.sql("""
        SELECT count(*) FROM 'https://data.source.coop/vida/google-microsoft-open-buildings/geoparquet/by_country/country_iso=AND/AND.parquet';
        """)

┌──────────────┐
│ count_star() │
│    int64     │
├──────────────┤
│         8279 │
└──────────────┘

In [3]:
dcb.sql("""
        DESCRIBE FROM 'https://data.source.coop/vida/google-microsoft-open-buildings/geoparquet/by_country/country_iso=AND/AND.parquet'
        """)

┌────────────────┬─────────────┬─────────┬─────────┬─────────┬─────────┐
│  column_name   │ column_type │  null   │   key   │ default │  extra  │
│    varchar     │   varchar   │ varchar │ varchar │ varchar │ varchar │
├────────────────┼─────────────┼─────────┼─────────┼─────────┼─────────┤
│ geometry       │ BLOB        │ YES     │ NULL    │ NULL    │ NULL    │
│ boundary_id    │ BIGINT      │ YES     │ NULL    │ NULL    │ NULL    │
│ bf_source      │ VARCHAR     │ YES     │ NULL    │ NULL    │ NULL    │
│ confidence     │ DOUBLE      │ YES     │ NULL    │ NULL    │ NULL    │
│ area_in_meters │ DOUBLE      │ YES     │ NULL    │ NULL    │ NULL    │
│ country_iso    │ VARCHAR     │ YES     │ NULL    │ NULL    │ NULL    │
└────────────────┴─────────────┴─────────┴─────────┴─────────┴─────────┘

In [4]:
dcb.sql("""
        SELECT DISTINCT bf_source 
              FROM 'https://data.source.coop/vida/google-microsoft-open-buildings/geoparquet/by_country/country_iso=AND/AND.parquet';
        """)


┌───────────┐
│ bf_source │
│  varchar  │
├───────────┤
│ microsoft │
└───────────┘

In [5]:
print(dcb.sql("""
        SELECT DISTINCT confidence 
              FROM 'https://data.source.coop/vida/google-microsoft-open-buildings/geoparquet/by_country/country_iso=AND/AND.parquet';
        """))

┌────────────┐
│ confidence │
│   double   │
├────────────┤
│       NULL │
└────────────┘



In [9]:
dcb.sql("""
    install spatial;
    load spatial;
     
    CREATE OR REPLACE TABLE test_buildings as SELECT bf_source, area_in_meters, ST_GeomFromWKB(geometry) as geom 
        FROM 'https://data.source.coop/vida/google-microsoft-open-buildings/geoparquet/by_country/country_iso=AND/AND.parquet';

    SELECT * FROM test_buildings;
    COPY test_buildings TO 'test_buildings.geojson' WITH (FORMAT GDAL, DRIVER 'GeoJSON', LAYER_CREATION_OPTIONS 'WRITE_BBOX=YES');
        """)


In [18]:
#View as dataframe
dcb.sql("SELECT * FROM test_buildings;").df().head(5)

bf_source  area_in_meters  \
0  microsoft      157.029426   
1  microsoft       67.900749   
2  microsoft      184.726518   
3  microsoft      303.451706   
4  microsoft      229.479454   

                                                geom  
0  [2, 4, 0, 0, 0, 0, 0, 0, 175, 77, 194, 63, 198...  
1  [2, 4, 0, 0, 0, 0, 0, 0, 216, 184, 193, 63, 24...  
2  [2, 4, 0, 0, 0, 0, 0, 0, 124, 67, 194, 63, 228...  
3  [2, 4, 0, 0, 0, 0, 0, 0, 56, 61, 203, 63, 220,...  
4  [2, 4, 0, 0, 0, 0, 0, 0, 107, 95, 194, 63, 184...

## Visualizing using Map
*package used - folium

In [2]:
import folium

In [9]:
geojson_file = "test_buildings.geojson"

# Create a Folium map centered at a specific location
locked_zoom = 11
fol_map = folium.Map(location=[42.5,1.6], zoom_start=locked_zoom,min_zoom = locked_zoom)

bounds = [[42.4, 1.2],[42.7, 1.9]]
fol_map.fit_bounds(bounds)
fol_map.options['maxBounds'] = bounds
# Add the GeoJSON data to the map
folium.GeoJson(geojson_file).add_to(fol_map)

In [11]:
fol_map

## Save as a html page

In [12]:
bounds_js = '''
<script>
    var map = L.map('map').setView([42.5,1.6], 11);
    var bounds = [[42.4, 1.2],[42.7, 1.9]];
    map.setMaxBounds(bounds);
    map.on('drag', function() {
        map.panInsideBounds(bounds, { animate: false });
    });
</script>
'''

# Adding the JavaScript to the map
fol_map.get_root().html.add_child(folium.Element(bounds_js))
fol_map.save("andorra_buildings_geojson.html")

In [ ]:

#dcb.sql("""
#    install spatial;
#    load spatial;
#     
#    CREATE OR REPLACE TABLE chennai_buildings as SELECT bf_source, area_in_meters, ST_GeomFromWKB(geometry) as geom 
#        FROM 'https://data.source.coop/vida/google-microsoft-open-buildings/geoparquet/by_country/country_iso=IND/IND.parquet' 
#        WHERE st_dwithin(geom,  st_point(80.3,13.1), .1);
#
#    SELECT * FROM chennai_buildings;
#    COPY chennai_buildings TO 'chennai_buildings.geojson' WITH (FORMAT GDAL, DRIVER 'GeoJSON', LAYER_CREATION_OPTIONS 'WRITE_BBOX=YES');
#        """)

#